In [1]:
'''Step 1:  remove the weird H NMRs '''

import torch, pickle, yaml
all_smiles_train = pickle.load(open('/workspace/SMILES_dataset/train/SMILES/index.pkl', 'rb'))
all_smiles_val = pickle.load(open('/workspace/SMILES_dataset/val/SMILES/index.pkl', 'rb'))
all_smiles_test = pickle.load(open('/workspace/SMILES_dataset/test/SMILES/index.pkl', 'rb'))

all_chemical_names_train = pickle.load(open('/workspace/SMILES_dataset/train/Chemical/index.pkl', 'rb'))
all_chemical_names_val = pickle.load(open('/workspace/SMILES_dataset/val/Chemical/index.pkl', 'rb'))
all_chemical_names_test = pickle.load(open('/workspace/SMILES_dataset/test/Chemical/index.pkl', 'rb'))

all_smiles_train_1d = pickle.load(open('/workspace/OneD_Only_Dataset/train/SMILES/index.pkl', 'rb'))
all_smiles_val_1d = pickle.load(open('/workspace/OneD_Only_Dataset/val/SMILES/index.pkl', 'rb'))
all_smiles_test_1d = pickle.load(open('/workspace/OneD_Only_Dataset/test/SMILES/index.pkl', 'rb'))

all_chemical_names_train_1d = pickle.load(open('/workspace/OneD_Only_Dataset/train/Chemical/index.pkl', 'rb'))
all_chemical_names_val_1d = pickle.load(open('/workspace/OneD_Only_Dataset/val/Chemical/index.pkl', 'rb'))
all_chemical_names_test_1d = pickle.load(open('/workspace/OneD_Only_Dataset/test/Chemical/index.pkl', 'rb'))


In [2]:
import os

weird_H_file_paths = []

all_maxes = set()

for split in ['train', 'val', 'test']:
    dir_1d = f'/workspace/OneD_Only_Dataset/'
    dir = f'/workspace/SMILES_dataset/'
    
    files = os.listdir(os.path.join(dir, split, "oneD_NMR"))
    
    for f in files:
        c_tensor, h_tensor = torch.load(f"{dir}/{split}/oneD_NMR/{f}")
        if len(h_tensor) and max(h_tensor)<0.5:
            # print(h_tensor)
            weird_H_file_paths.append(f"{dir}/{split}/oneD_NMR/{f}")
        if len(h_tensor) and max(h_tensor)>0.5 :
            all_maxes.add(max(h_tensor))
            
    files = os.listdir(os.path.join(dir_1d, split, "oneD_NMR"))
    for f in files:
        c_tensor, h_tensor = torch.load(f"{dir_1d}/{split}/oneD_NMR/{f}")
        if len(h_tensor) and max(h_tensor)<0.5:
            # print(h_tensor)
            weird_H_file_paths.append(f"{dir_1d}/{split}/oneD_NMR/{f}")
        if len(h_tensor) and max(h_tensor)>0.5 :
            all_maxes.add(max(h_tensor)) 
    

In [3]:
min(all_maxes), len(weird_H_file_paths)

(tensor(0.8900), 1)

In [4]:
import json 
with open('/root/gurusmart/data/NP-MRD-dataset/NP-MRD_metadata/npmrd_natural_products.json') as f:
    data = json.load(f)
names_to_npmrd_id = dict([[d['name'], d['accession'] ]for d in data['np_mrd']['natural_product']])


In [5]:
import pickle
from pathlib import Path
NP_to_smiles, NP_to_names = pickle.load(open(Path('/root/gurusmart/data/NP_to_smiles_and_names.pkl'), 'rb'))

print(len(NP_to_smiles), len(set(NP_to_smiles.values())))

280242 279454


In [6]:
from collections import defaultdict
smiles_to_NP = defaultdict(list)
for k,v in NP_to_smiles.items():
    smiles_to_NP[v].append(k)

In [7]:
unmatched_smiles = []
for f_weird in (weird_H_file_paths):
    # c_tensor, h_tensor = torch.load(f_weird)
    file_idx = int(f_weird.split('/')[-1].split('.')[0])
    if 'OneD_Only' in f_weird:
        if 'train' in f_weird:
            smiles = all_smiles_train_1d[file_idx]
        elif 'val' in f_weird:
            smiles = all_smiles_val_1d[file_idx]
        elif 'test' in f_weird:
            smiles = all_smiles_test_1d[file_idx]
    else:
        if 'train' in f_weird:
            smiles = all_smiles_train[file_idx]
        elif 'val' in f_weird:
            smiles = all_smiles_val[file_idx]
        elif 'test' in f_weird:
            smiles = all_smiles_test[file_idx]
    print(smiles_to_NP[smiles])

['NP0212394']


In [8]:
smiles_and_id = ([[d['name'], d['accession'] ]for d in data['np_mrd']['natural_product']])

In [9]:
import os

def delete_H(file_path):
    c_tensor, h_tensor = torch.load(file_path)
    if len(c_tensor) == 0:
        os.remove(file_path)
        return True
    torch.save((c_tensor, torch.tensor([])), file_path)

# Example usage
for i in weird_H_file_paths:
    delete_H(i)


In [10]:
len(weird_H_file_paths)

1

In [11]:
'''make sure deleted'''

weird_H_file_paths_make_sure = []

all_maxes = set()

for split in ['train', 'val', 'test']:
    dir_1d = f'/workspace/OneD_Only_Dataset/'
    dir = f'/workspace/SMILES_dataset/'
    
    files = os.listdir(os.path.join(dir, split, "oneD_NMR"))
    
    for f in files:
        c_tensor, h_tensor = torch.load(f"{dir}/{split}/oneD_NMR/{f}")
        if len(h_tensor) and max(h_tensor)<0.5:
            # print(h_tensor)
            weird_H_file_paths_make_sure.append(f"{dir}/{split}/oneD_NMR/{f}")
       
            
    files = os.listdir(os.path.join(dir_1d, split, "oneD_NMR"))
    for f in files:
        c_tensor, h_tensor = torch.load(f"{dir_1d}/{split}/oneD_NMR/{f}")
        if len(h_tensor) and max(h_tensor)<0.5:
            # print(h_tensor)
            weird_H_file_paths_make_sure.append(f"{dir_1d}/{split}/oneD_NMR/{f}")
    

In [12]:
weird_H_file_paths_make_sure

[]

In [13]:
for split in ['train', 'val', 'test']:
    path_to_load_full_info_indices = f"/root/gurusmart/MorganFP_prediction/reproduce_previous_works/smart4.5/datasets/{split}_indices_of_full_info_NMRs.pkl"
    all_info_files = pickle.load(open(path_to_load_full_info_indices, "rb"))
    
    deleted=[]
    for w in weird_H_file_paths:
        if w.startswith("/workspace/SMILES_dataset//train"):
            deleted.append(w.split("/oneD_NMR/")[-1])
            
    print("interseciton : ", set(all_info_files).intersection(set(deleted)))
    print(len(set(all_info_files).intersection(set(deleted))))
    

interseciton :  set()
0
interseciton :  set()
0
interseciton :  set()
0


In [14]:
'''Step 2:  remove the duplicates where they have the exact same NMRs'''

'Step 2:  remove the duplicates where they have the exact same NMRs'

In [15]:
from collections import defaultdict
import tqdm, os, torch
oneD_tensors_to_file_paths = defaultdict(list)
for split in ['train', 'val', 'test']:
    dir_1d = f'/workspace/OneD_Only_Dataset/'
    dir = f'/workspace/SMILES_dataset/'
    
    files = os.listdir(os.path.join(dir, split, "oneD_NMR"))
    
    for f in files:
        c_tensor, h_tensor = torch.load(f"{dir}/{split}/oneD_NMR/{f}")
        clist = c_tensor.tolist()
        hlist = h_tensor.tolist()
        clist.sort()
        hlist.sort()
        oneD_tensors_to_file_paths[(tuple(clist), tuple(hlist))].append(f"{dir}/{split}/oneD_NMR/{f}")
            
    files = os.listdir(os.path.join(dir_1d, split, "oneD_NMR"))
    for f in tqdm.tqdm(files):
        c_tensor, h_tensor = torch.load(f"{dir_1d}/{split}/oneD_NMR/{f}")
        clist = c_tensor.tolist()
        hlist = h_tensor.tolist()
        clist.sort()
        hlist.sort()
        oneD_tensors_to_file_paths[(tuple(clist), tuple(hlist))].append(f"{dir_1d}/{split}/oneD_NMR/{f}")
        

100%|██████████| 8219/8219 [00:01<00:00, 4117.09it/s]


In [16]:
for k, v in oneD_tensors_to_file_paths.items():
    if len(v) > 1:
     
        print(v)

['/workspace/SMILES_dataset//train/oneD_NMR/83601.pt', '/workspace/OneD_Only_Dataset//test/oneD_NMR/10041.pt']
['/workspace/SMILES_dataset//train/oneD_NMR/67376.pt', '/workspace/SMILES_dataset//train/oneD_NMR/67604.pt']
['/workspace/SMILES_dataset//train/oneD_NMR/68122.pt', '/workspace/SMILES_dataset//train/oneD_NMR/68046.pt']
['/workspace/SMILES_dataset//train/oneD_NMR/33604.pt', '/workspace/SMILES_dataset//val/oneD_NMR/4290.pt']
['/workspace/SMILES_dataset//train/oneD_NMR/37217.pt', '/workspace/SMILES_dataset//train/oneD_NMR/37216.pt']
['/workspace/SMILES_dataset//train/oneD_NMR/3291.pt', '/workspace/SMILES_dataset//train/oneD_NMR/3290.pt']
['/workspace/SMILES_dataset//train/oneD_NMR/67999.pt', '/workspace/SMILES_dataset//train/oneD_NMR/68012.pt', '/workspace/OneD_Only_Dataset//train/oneD_NMR/109122.pt', '/workspace/OneD_Only_Dataset//train/oneD_NMR/106133.pt', '/workspace/OneD_Only_Dataset//train/oneD_NMR/70837.pt', '/workspace/OneD_Only_Dataset//train/oneD_NMR/63960.pt', '/workspac

In [17]:
def find_index_of_2d(paths):
    for i, p in enumerate(paths):
        if "SMILES_dataset" in p:
            return i
    return -1

path_to_delete_because_of_duplicates = []
sum_v = 0
for k, v in oneD_tensors_to_file_paths.items():
    sum_v+=len(v)
    if len(v) > 1:
        first_2d = find_index_of_2d(v)
        if first_2d == -1:
            path_to_delete_because_of_duplicates.extend(v[1:])
            continue
        path_to_delete_because_of_duplicates.extend(v[0:first_2d])
        path_to_delete_because_of_duplicates.extend(v[first_2d+1:])


In [18]:
len(path_to_delete_because_of_duplicates), len(oneD_tensors_to_file_paths), sum_v

(40592, 150738, 191330)

In [19]:
path_to_delete_because_of_duplicates[:3]

['/workspace/OneD_Only_Dataset//test/oneD_NMR/10041.pt',
 '/workspace/SMILES_dataset//train/oneD_NMR/67604.pt',
 '/workspace/SMILES_dataset//train/oneD_NMR/68046.pt']

In [20]:
for i in path_to_delete_because_of_duplicates:
    os.remove(i)

In [21]:
'''make sure deleted'''

from collections import defaultdict
import tqdm
oneD_tensors_to_file_paths = defaultdict(list)
for split in ['train', 'val', 'test']:
    dir_1d = f'/workspace/OneD_Only_Dataset/'
    dir = f'/workspace/SMILES_dataset/'
    
    files = os.listdir(os.path.join(dir, split, "oneD_NMR"))
    
    for f in files:
        c_tensor, h_tensor = torch.load(f"{dir}/{split}/oneD_NMR/{f}")
        clist = c_tensor.tolist()
        hlist = h_tensor.tolist()
        clist.sort()
        hlist.sort()
        oneD_tensors_to_file_paths[(tuple(clist), tuple(hlist))].append(f"{dir}/{split}/oneD_NMR/{f}")
            
    files = os.listdir(os.path.join(dir_1d, split, "oneD_NMR"))
    for f in tqdm.tqdm(files):
        c_tensor, h_tensor = torch.load(f"{dir_1d}/{split}/oneD_NMR/{f}")
        clist = c_tensor.tolist()
        hlist = h_tensor.tolist()
        clist.sort()
        hlist.sort()
        oneD_tensors_to_file_paths[(tuple(clist), tuple(hlist))].append(f"{dir_1d}/{split}/oneD_NMR/{f}")
        

100%|██████████| 5327/5327 [00:01<00:00, 4123.37it/s]


In [22]:
for k, v in oneD_tensors_to_file_paths.items():
    if len(v) > 1:
     
        print(v)

In [24]:
torch.load('/workspace/SMILES_dataset//train/oneD_NMR/1004.pt'), all_smiles_train[1004],

([tensor([ 33.1400,  34.4000, 126.0700, 131.4000,  37.6600,  39.3000, 154.7000,
          171.3000,  11.1300, 142.7000, 143.1500,  24.4400, 185.1000,  26.0800,
          126.2000]),
  tensor([1.5800, 2.8300, 1.3300, 1.7200, 5.9400, 6.6200, 6.1900, 1.8800, 2.4400])],
 'C=C(C(=O)O)C1CCC2(C)C=CC(=O)C(C)=C2C1')